In [4]:
import numpy as np
from numba import njit
from functools import partial
import talib 
import pandas as pd
import vectorbt as vbt
import vectorbt as vbt
from vectorbt.utils.colors import adjust_opacity
from vectorbt.utils.enum_ import map_enum_fields
from vectorbt.base.reshape_fns import broadcast, flex_select_auto_nb, to_2d_array
from vectorbt.portfolio.enums import SizeType, Direction, NoOrder, OrderStatus, OrderSide
from vectorbt.portfolio import nb
import sys
import os
function_essential_path = r"C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\FunctionEssential"
function_s_score_path = r'C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\Indicateur'
sys.path.append(function_essential_path)
sys.path.append(function_s_score_path)
import utils as us
import s_score as score

In [5]:
##FONCTION##

In [41]:
##FONCTION LOGIQUE SIGNALS##

def entries_trades(close,sscore,adx_h4,adx_d1,rsi,seuil_score,seuil_adx):
    long = np.full_like(close, False, dtype=bool)
    short = np.full_like(close, False, dtype=bool)
    trade_out = True

    for col in range(sscore.shape[1]):
        for idx in range(len(close)-1):

            if (adx_h4[idx, col] <= seuil_adx) & (adx_d1[idx, col] <= seuil_adx):
                if trade_out:
                    if sscore[idx, col] <= -seuil_score:
                            if rsi[idx, col] <= 30:
                                long[idx, col] = True
                                trade_out = False
                    if sscore[idx, col] >= seuil_score:
                            if rsi[idx, col] >= 70:
                                short[idx, col] = True
                                trade_out = False
                else:
                    if (sscore[idx, col] <= 0.5) & (sscore[idx, col] >= -0.5):
                        trade_out = True
    
    return long, short


# def entries_trades(close,sscore,adx_h4,adx_d1,rsi,seuil_score,adx_period,seuil_adx):
#     long = np.full_like(close, False, dtype=bool)
#     short = np.full_like(close, False, dtype=bool)
#     trade_out = True



    
#     for idx in range(len(close)):

#         if (adx_h4[idx] <= seuil_adx) & (adx_d1[idx] <= seuil_adx):
#             if trade_out:
#                 if sscore[idx] <= -seuil_score:
#                     if rsi[idx] <= 30:
#                         long[idx] = True
#                         trade_out = False
#                 if sscore[idx] >= seuil_score:
#                     if rsi[idx] >= 70:
#                         short[idx] = True
#                         trade_out = False
#             else:
#                 if (sscore[idx] <= 0.5) & (sscore[idx] >= -0.5):
#                     trade_out = True
#     return long,short

def exits_trades(long,short,close,sscore,seuil_sscore_out,seuil_sl):
    long_exit = np.zeros_like(long, dtype=np.float64)
    short_exit = np.zeros_like(short, dtype=np.float64)
    for col in range(long.shape[1]):

        for idx in range(len(close)):
            
            if long[idx, col]:
                SL = close[idx, col] * (1-seuil_sl)
                for j in range(idx+1,len(close)):
                    if close[j, col] <= SL:
                        long_exit[j, col] = SL
                        break
                    if sscore[j, col] >= -seuil_sscore_out:
                        long_exit[j, col] = close[j, col]
                        break


            if short[idx, col]:

                SL = close[idx, col] * (1+seuil_sl)
                for j in range(idx+1,len(close)):
                    if close[j, col] >= SL:
                        short_exit[j, col] = SL
                        break

                    if sscore[j, col] <= seuil_sscore_out:
                        short_exit[j, col] = close[j, col]
                        break



    return long_exit,short_exit


In [42]:
##INDICATEUR FACTORY##

Entry = vbt.IndicatorFactory(
    class_name="entries_trades",
    input_names=["close","sscore","adx_h4","adx_d1","rsi"],
    param_names=["seuil_score","seuil_adx"],
    output_names=["long","short"],
).from_apply_func(entries_trades)

Exit = vbt.IndicatorFactory(
    class_name="exits_trades",
    input_names=["long","short","close","sscore"],
    param_names=["seuil_sscore_out","seuil_sl"],
    output_names=["long","short"],
).from_apply_func(exits_trades)

In [43]:
@njit
def pre_sim_func_nb(c):
    entry_price = np.full(c.target_shape[1], np.nan, dtype=np.float64)  
    return (entry_price,)

@njit
def order_func_nb(c, entry_price, long, short, long_exit,short_exit, size):
    price_now = nb.get_elem_nb(c, c.close)
    entry_long_now = nb.get_elem_nb(c, long)
    entry_short_now = nb.get_elem_nb(c, short)


    if entry_long_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.001
            )
        elif c.position_now < 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )  

    if entry_short_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.001
            )
        elif c.position_now > 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    #Si la valeur de l'idx de la sortie est différente de 0 ca veut dire que on doit out et on récupere la valeur de notre np.array long_exit 
    if c.position_now > 0:
        long_exit_now = nb.get_elem_nb(c, long_exit)
        if long_exit_now != 0:
            return nb.order_nb(
                -size[c.col],
                price=long_exit_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now < 0:
        short_exit_now = nb.get_elem_nb(c, short_exit)
        if short_exit_now != 0:
            return nb.order_nb(
                -size[c.col],
                price=short_exit_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )
       

    return NoOrder

@njit
def post_order_func_nb(c, entry_price):
    if c.order_result.status == OrderStatus.Filled:
        entry_price[c.col] = c.order_result.price

In [65]:
##CLASS STRATEGIE##

class Strategie():

    def __init__(self,data,tickers,frequence):
        self.data = data
        self.tickers = tickers
        self.frequences = frequence


    def set_params_strategie(self,sl,out,sscore_seuil,sscore,rsi_period,adx_period,seuil_adx,mf):
        self.stop_loss = sl 
        self.sscore_out = out
        self.sscore_seuil = sscore_seuil
        self.sscore = sscore
        self.rsi_period = rsi_period
        self.adx_period = adx_period
        self.seuil_adx = seuil_adx
        self.main_frequence = mf
        


    def backtest(self):

            entries_long_df = pd.DataFrame()   
            entries_short_df = pd.DataFrame()
            exits_long_df = pd.DataFrame()
            exits_short_df = pd.DataFrame()
            close_df = pd.DataFrame()
            datetime_df = pd.DataFrame()

            for ticker in self.tickers:

                data = self.data[self.main_frequence][ticker]
                datetime = data.reset_index()['Datetime']


                rsi = vbt.RSI.run(data['close'], window=self.rsi_period).rsi

                adx_h4 = []
                adx_d1 = []

                for period in self.adx_period:
                    adx_h4.append(talib.ADX(data['high'], data['low'], data['close'], timeperiod=period))
                    adx_d1.append(talib.ADX(self.data['D1'][ticker]['high'], self.data['D1'][ticker]['low'], self.data['D1'][ticker]['close'], timeperiod=period))

                
                adx_h4 = pd.DataFrame(adx_h4).T 
                adx_d1 = pd.DataFrame(adx_d1).T
                adx_d1_reshape = us.resample_shape_frequence(data['close'], adx_d1)


                s_score_ajuster = self.sscore[ticker]['adjusted_s_scores_vol']

                us.get_details_variable([adx_h4,adx_d1_reshape,s_score_ajuster,data['close'],rsi,self.sscore_seuil,self.seuil_adx])
                
                trades = Entry.run(
                    data['close'],
                    s_score_ajuster,
                    adx_h4,
                    adx_d1_reshape,
                    rsi,
                    self.sscore_seuil,
                    self.seuil_adx
                )

                exit = Exit.run(
                    trades.long,
                    trades.short,
                    data['close'],
                    s_score_ajuster,
                    self.sscore_out,
                    self.stop_loss
                )

                us.print_trades(trades.long,trades.short,None,None,data)

                entries_long_df[ticker] = trades.long.reset_index(drop=True)
                entries_short_df[ticker] = trades.short.reset_index(drop=True)
                exits_long_df[ticker] = exit.long.reset_index(drop=True)
                exits_short_df[ticker] = exit.short.reset_index(drop=True)
                close_df[ticker] = data['close'].reset_index(drop=True)
                datetime_df[ticker] = datetime.reset_index(drop=True)

                

            size = np.array([600000]*len(self.tickers))
            exits_long_df = exits_long_df.astype(np.float64).fillna(0)
            exits_short_df = exits_short_df.astype(np.float64).fillna(0)
            s_score_ajuster = np.asarray(s_score_ajuster, dtype=np.float64).reshape(-1,1)
            
            portfolio = vbt.Portfolio.from_order_func(
                close_df,  
                order_func_nb,  
                entries_long_df.values,  
                entries_short_df.values,  
                exits_long_df.values,
                exits_short_df.values,
                size,  
                freq=self.frequences,  
                init_cash=100000,  # Ajout du capital initial
                pre_sim_func_nb=pre_sim_func_nb,  
                post_order_func_nb=post_order_func_nb,  
                broadcast_named_args=dict(  
                    long=entries_long_df.values,  
                    short=entries_short_df.values,  
                    exits_long_df=exits_long_df.values,  
                    exits_short_df=exits_short_df.values,  
                    size=size  
                )
            )
            us.rapport_backtest(portfolio,close_df,datetime_df,self.tickers)
            return portfolio

    def optimize(self,fitness_func,ticker,choice,close,high,low,close_D1,high_D1,low_D1,ssscore,params1,params2):
        if choice == 1:
            #Profil periode RSI


            data = self.data[self.main_frequence][ticker]
            datetime = data.reset_index()['Datetime']
            rsi = vbt.RSI.run(close, window=params1).rsi

            adx_h4 = []
            adx_d1 = []

            for period in self.adx_period:
                adx_h4.append(talib.ADX(high, low, close, timeperiod=period))
                adx_d1.append(talib.ADX(high_D1, low_D1, close_D1, timeperiod=period))

            
            adx_h4 = pd.DataFrame(adx_h4).T 
            adx_d1 = pd.DataFrame(adx_d1).T
            adx_d1_reshape = us.resample_shape_frequence(close, adx_d1)


            trades = Entry.run(
                close,
                ssscore,
                adx_h4,
                adx_d1_reshape,
                rsi,
                self.sscore_seuil,
                self.seuil_adx
            )

            exit = Exit.run(
                trades.long,
                trades.short,
                close,
                ssscore,
                self.sscore_out,
                self.stop_loss,
                param_product=True
            )

            long = trades.long
            short = trades.short
            long_exit = exit.long
            short_exit = exit.short


            long = long.reset_index(drop=True)
            short = short.reset_index(drop=True)
            long_exit = long_exit.reset_index(drop=True)
            short_exit = short_exit.reset_index(drop=True)
            close = close.reset_index(drop=True)
            close = pd.DataFrame(close)  

            size = np.array([600000]*long_exit.shape[1])



            portfolio = vbt.Portfolio.from_order_func(
                close,  
                order_func_nb,  
                long.values,  
                short.values,  
                long_exit.values,
                short_exit.values,
                size,  
                freq=self.frequences,  
                init_cash=100000,  
                pre_sim_func_nb=pre_sim_func_nb,  
                post_order_func_nb=post_order_func_nb,  
                broadcast_named_args=dict(  
                    long=long.values,  
                    short=short.values,  
                    exits_long_df=long_exit.values,  
                    exits_short_df=short_exit.values,  
                    size=size  
                )
            )
            
            # perf = us.get_heatmap(portfolio,combinaison,fitness_func)
            # us.get_3d_surface_metrics(2,portfolio,combinaison,fitness_func,"Sscore out ","Sl ",15,40)
            perf = us.get_barplot(portfolio,params1,fitness_func)
            param1,param2,metrics = us.get_best_param(perf)
            return param1,param2
        
        if choice == 2:
            #Profil periode ADX


            data = self.data[self.main_frequence][ticker]
            datetime = data.reset_index()['Datetime']
            rsi = vbt.RSI.run(close, window=self.rsi_period).rsi

            adx_h4 = []
            adx_d1 = []

            for period in params1:
                adx_h4.append(talib.ADX(high, low, close, timeperiod=period))
                adx_d1.append(talib.ADX(high_D1, low_D1, close_D1, timeperiod=period))

            
            adx_h4 = pd.DataFrame(adx_h4).T 
            adx_d1 = pd.DataFrame(adx_d1).T
            adx_d1_reshape = us.resample_shape_frequence(close, adx_d1)


            trades = Entry.run(
                close,
                ssscore,
                adx_h4,
                adx_d1_reshape,
                rsi,
                self.sscore_seuil,
                self.seuil_adx
            )

            exit = Exit.run(
                trades.long,
                trades.short,
                close,
                ssscore,
                self.sscore_out,
                self.stop_loss,
                param_product=True
            )

            long = trades.long
            short = trades.short
            long_exit = exit.long
            short_exit = exit.short


            long = long.reset_index(drop=True)
            short = short.reset_index(drop=True)
            long_exit = long_exit.reset_index(drop=True)
            short_exit = short_exit.reset_index(drop=True)
            close = close.reset_index(drop=True)
            close = pd.DataFrame(close)  

            size = np.array([600000]*long_exit.shape[1])



            portfolio = vbt.Portfolio.from_order_func(
                close,  
                order_func_nb,  
                long.values,  
                short.values,  
                long_exit.values,
                short_exit.values,
                size,  
                freq=self.frequences,  
                init_cash=100000,  
                pre_sim_func_nb=pre_sim_func_nb,  
                post_order_func_nb=post_order_func_nb,  
                broadcast_named_args=dict(  
                    long=long.values,  
                    short=short.values,  
                    exits_long_df=long_exit.values,  
                    exits_short_df=short_exit.values,  
                    size=size  
                )
            )
            
            # perf = us.get_heatmap(portfolio,combinaison,fitness_func)
            # us.get_3d_surface_metrics(2,portfolio,combinaison,fitness_func,"Sscore out ","Sl ",15,40)
            perf = us.get_barplot(portfolio,params1,fitness_func)
            param1,param2,metrics = us.get_best_param(perf)
            return param1,param2

        if choice == 3:
            #Optimisation de la periode différer entre H4 et D1

            combinaison=[]

            for i in params1:
                for j in params2:
                    combinaison.append((i,j))

            data = self.data[self.main_frequence][ticker]
            datetime = data.reset_index()['Datetime']
            rsi = vbt.RSI.run(close, window=self.rsi_period).rsi

            adx_h4 = []
            adx_d1 = []

            for period in self.adx_period:
                adx_h4.append(talib.ADX(high, low, close, timeperiod=period))
                adx_d1.append(talib.ADX(high_D1, low_D1, close_D1, timeperiod=period))

            
            adx_h4 = pd.DataFrame(adx_h4).T 
            adx_d1 = pd.DataFrame(adx_d1).T
            adx_d1_reshape = us.resample_shape_frequence(close, adx_d1)


            trades = Entry.run(
                close,
                ssscore,
                adx_h4,
                adx_d1_reshape,
                rsi,
                self.sscore_seuil,
                self.seuil_adx
            )

            exit = Exit.run(
                trades.long,
                trades.short,
                close,
                ssscore,
                params1,
                params2,
                param_product=True
            )

            long = trades.long
            short = trades.short
            long_exit = exit.long
            short_exit = exit.short


            long = long.reset_index(drop=True)
            short = short.reset_index(drop=True)
            long_exit = long_exit.reset_index(drop=True)
            short_exit = short_exit.reset_index(drop=True)
            close = close.reset_index(drop=True)
            close = pd.DataFrame(close)  

            size = np.array([1000]*long_exit.shape[1])



            portfolio = vbt.Portfolio.from_order_func(
                close,  
                order_func_nb,  
                long.values,  
                short.values,  
                long_exit.values,
                short_exit.values,
                size,  
                freq=self.frequences,  
                init_cash=100000,  
                pre_sim_func_nb=pre_sim_func_nb,  
                post_order_func_nb=post_order_func_nb,  
                broadcast_named_args=dict(  
                    long=long.values,  
                    short=short.values,  
                    exits_long_df=long_exit.values,  
                    exits_short_df=short_exit.values,  
                    size=size  
                )
            )
            
            perf = us.get_heatmap(portfolio,combinaison,fitness_func)
            us.get_3d_surface_metrics(2,portfolio,combinaison,fitness_func,"Sscore out ","Sl ",15,40)
            param1,param2,metrics = us.get_best_param(perf)
            return param1,param2


    def wfa(self,period_OOS, period_IOS):
 
        close_df = pd.DataFrame()
        for ticker in self.tickers:

            data = self.data[self.main_frequence][ticker]
            cycle = us.generate_wf_cycles(data, period_IOS, period_OOS)
            close = data['close']
            s_score_ajuster = self.sscore[ticker]['adjusted_s_scores_vol']
            close_df['close'] = close

            for i in range(len(cycle)):

                close_IOS = data["close"].iloc[cycle[i][0]:cycle[i][1]]
                close_OOS = data["close"].iloc[cycle[i][2]:cycle[i][3]]
                high_IOS = data["high"].iloc[cycle[i][0]:cycle[i][1]]
                high_OOS = data["high"].iloc[cycle[i][2]:cycle[i][3]]
                low_IOS = data["low"].iloc[cycle[i][0]:cycle[i][1]]
                low_OOS = data["low"].iloc[cycle[i][2]:cycle[i][3]]

                close_IOS_D1 = data["close"].iloc[cycle[i][0]:cycle[i][1]]
                close_OOS_D1 = data["close"].iloc[cycle[i][2]:cycle[i][3]]
                high_IOS_D1 = data["high"].iloc[cycle[i][0]:cycle[i][1]]
                high_OOS_D1 = data["high"].iloc[cycle[i][2]:cycle[i][3]]
                low_IOS_D1 = data["low"].iloc[cycle[i][0]:cycle[i][1]]
                low_OOS_D1 = data["low"].iloc[cycle[i][2]:cycle[i][3]]
                datetime_D1 = data.reset_index()['Datetime']


                s_score_ajuster_IOS = s_score_ajuster.iloc[cycle[i][0]:cycle[i][1]].reset_index(drop=True)
                s_score_ajuster_OOS = s_score_ajuster.iloc[cycle[i][2]:cycle[i][3]].reset_index(drop=True)



                adx_h4 = []
                adx_d1 = []
                adx_h4_ios = []
                adx_d1_ios = []

                for period in self.adx_period:
                    adx_h4.append(talib.ADX(high_OOS, low_OOS, close_OOS, timeperiod=period))
                    adx_d1.append(talib.ADX(high_OOS_D1, low_OOS_D1,close_OOS_D1, timeperiod=period))

                rsi = vbt.RSI.run(close_OOS, window=self.rsi_period).rsi
                adx_h4 = pd.DataFrame(adx_h4).T 
                adx_d1 = pd.DataFrame(adx_d1).T
                adx_d1_reshape = us.resample_shape_frequence(close_OOS, adx_d1)


                if ticker == "EURUSD":
                    sscore_out = np.round(np.arange(0,-2.2,-0.2),1)
                    sl = np.round(np.arange(0.01, 0.025,0.002),3)
                
                if ticker == "GPDUSD":
                    sscore_out = np.round(np.arange(-0.4,-2,-0.2),1)
                    sl = np.round(np.arange(0.01, 0.025,0.002),3)
                
                if ticker == "USDJPY":
                    sscore_out = np.round(np.arange(0,-1.2,-0.2),1)
                    sl = np.round(np.arange(0.01, 0.022,0.002),3)


                
                out_opti,sl_opti=self.optimize(2,ticker,3,close_IOS,high_IOS,low_IOS,close_IOS_D1,high_IOS_D1,low_IOS_D1,s_score_ajuster_IOS,sscore_out,sl)
                

                if i == 0:

                    for period in self.adx_period:
                        adx_h4_ios.append(talib.ADX(high_IOS, low_IOS, close_IOS, timeperiod=period))
                        adx_d1_ios.append(talib.ADX(high_IOS_D1, low_IOS_D1,close_IOS_D1, timeperiod=period))

                    rsi_ios = vbt.RSI.run(close_IOS, window=self.rsi_period).rsi
                    adx_h4_ios = pd.DataFrame(adx_h4_ios).T 
                    adx_d1_ios = pd.DataFrame(adx_d1_ios).T
                    adx_d1_ios_reshape = us.resample_shape_frequence(close_IOS, adx_d1_ios)

                    trades = Entry.run(
                        close_IOS,
                        s_score_ajuster_IOS,
                        adx_h4_ios,
                        adx_d1_ios_reshape,
                        rsi_ios,
                        self.sscore_seuil,
                        self.seuil_adx
                    )

                    exit = Exit.run(
                        trades.long,
                        trades.short,
                        close_IOS,
                        s_score_ajuster_IOS,
                        out_opti,
                        sl_opti
                    )

                    entries_long = trades.long.squeeze()  # Convertir en Series
                    entries_short = trades.short.squeeze()
                    exits_long = exit.long.squeeze()
                    exits_short = exit.short.squeeze()



                trades = Entry.run(
                    close_OOS,
                    s_score_ajuster_OOS,
                    adx_h4,
                    adx_d1_reshape,
                    rsi,
                    self.sscore_seuil,
                    self.seuil_adx
                )

                exit = Exit.run(
                    trades.long,
                    trades.short,
                    close_OOS,
                    s_score_ajuster_OOS,
                    out_opti,
                    sl_opti
                )


                entries_long = pd.concat([entries_long,  pd.Series(trades.long.squeeze())], ignore_index=True)
                entries_short = pd.concat([entries_short,  pd.Series(trades.short.squeeze())], ignore_index=True)
                exits_long = pd.concat([exits_long,  pd.Series(exit.long.squeeze())], ignore_index=True)
                exits_short = pd.concat([exits_short,  pd.Series(exit.short.squeeze())], ignore_index=True)



            capital = 100000   
            size = np.array([(0.05 * capital) / (0.02 * close_df.iloc[0, i]) for i in range(len(self.tickers))])

            portfolio = vbt.Portfolio.from_order_func(
                close,  
                order_func_nb,  
                entries_long.values,  
                entries_short.values,  
                exits_long.values,
                exits_short.values,
                size,  
                freq=self.frequences,  
                init_cash=100000,  # Ajout du capital initial
                pre_sim_func_nb=pre_sim_func_nb,  
                post_order_func_nb=post_order_func_nb,  
                broadcast_named_args=dict(  
                    long=entries_long.values,  
                    short=entries_short.values,  
                    exits_long=exits_long.values,  
                    exits_short=exits_short.values,  
                    size=size  
                )
            )

            us.get_pnl(portfolio)


            us.rapport_backtest(portfolio,close_df,None,['close'])
            return portfolio



In [72]:
tickers = ['GPDUSD']
DATA = us.get_data_forex(tickers,['H4','D1'],"2000-01-01","2017-01-01")
s_score_value = {}
for ticker in tickers:
    data_traitement = DATA['H4'][ticker]
    nb_nan = data_traitement['close'].isna().sum()
    close = data_traitement['close'].dropna()
    close_without_index = close.reset_index()
    result = score.mean_reversion(close, close_without_index['Datetime'], 85, "VOL", 0.5, "EGARCH")
    result_df = pd.DataFrame({
        's_score_value': result[0],
        'adjusted_s_scores_vol': result[1],
        'theta_vals': result[2],
        'mu_vals': result[3],
        'sigma_vals': result[4]
    })
    nan_rows = pd.DataFrame([[float('nan')] * result_df.shape[1]] * nb_nan, columns=result_df.columns)
    result_df = pd.concat([result_df, nan_rows], ignore_index=True)
    s_score_value[ticker] = result_df

  0%|          | 0/23157 [00:00<?, ?it/s]

Estimation des paramètres OU:   0%|          | 0/36224 [01:10<?, ?it/s]
C:\Users\Jordi\Desktop\Environement de developement\Trading_Dev_Stratégie_Environement\Indicateur\s_score.py:31: RuntimeWarning:

invalid value encountered in sqrt

Calcul de la volatilité conditionnelle:   0%|          | 0/23242 [00:00<?, ?it/s]c:\Users\Jordi\AppData\Local\Programs\Python\Python312\Lib\site-packages\arch\univariate\base.py:768: ConvergenceWarning:

The optimizer returned code 4. The message is:
Inequality constraints incompatible
See scipy.optimize.fmin_slsqp for code meaning.


Calcul de la volatilité conditionnelle: 100%|██████████| 23242/23242 [00:00<00:00, 320306.54it/s]


23241


C:\Users\Jordi\AppData\Local\Temp\ipykernel_14396\3072032119.py:18: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [ ]:
strat = Strategie(DATA,tickers,"240m")
strat.set_params_strategie(0.0,-1,3,s_score_value,20,[40],25,'H4')
portfolio = strat.backtest()

# data_4h = DATA['H4']['GPDUSD']
# data_d1 = DATA['D1']['GPDUSD']

# # # # seuil_sscore = np.round(np.arange(1,4.2,0.2),1)
# # # # seuil_adx = np.arange(15,31,1)

# # # sscore_out = np.round(np.arange(2,-4.2,-0.2),1)
# # # sl = np.round(np.arange(0.01, 0.05,0.002),3)

# adx_period = np.arange(10,61,1)
# params=strat.optimize(2,'GPDUSD',2,data_4h['close'],data_4h['high'],data_4h['low'],data_d1['low'],data_d1['low'],data_d1['low'],s_score_value['GPDUSD']['adjusted_s_scores_vol'],adx_period,None)
# rsi_period = np.arange(5,31,1)
# params=strat.optimize(2,'GPDUSD',1,data_4h['close'],data_4h['high'],data_4h['low'],data_d1['low'],data_d1['low'],data_d1['low'],s_score_value['GPDUSD']['adjusted_s_scores_vol'],rsi_period,None)
# # # # print(sl)
# # # # print(out)

# # strat.wfa("5Y","10Y")

Variable : N/A
Type : <class 'pandas.core.frame.DataFrame'>
Shape : (36309, 1)


Variable : N/A
Type : <class 'pandas.core.frame.DataFrame'>
Shape : (36309, 1)


Variable : adjusted_s_scores_vol
Type : <class 'pandas.core.series.Series'>
Shape : (36309,)


Variable : close
Type : <class 'pandas.core.series.Series'>
Shape : (36309,)


Variable : (20, 'close')
Type : <class 'pandas.core.series.Series'>
Shape : (36309,)


Variable : N/A
Type : <class 'int'>
Shape : N/A


Variable : N/A
Type : <class 'int'>
Shape : N/A





------------------------------------------------------------------DETAILS : GPDUSD-----------------------------------------------------------------

Total Return : 11.17%
Benchmark return : -19.78%
CAGR : 0.64%
Volatility : 18.38%
Sharpe Ratio : 0.13
Benchmark sharpe ratio : -0.02
Max Drawdown: -48.1%
Calmar Ratio : 0.01
Beta : -0.3


Total trades : 67
Total long trades 35
Total short trades 32
Win rate : 0.57%
Wining streak : 7.0
Loosing streak : 6.0
Average winning trade : 2.0%
Average losing trade : -2.0%
Profit factor : 1.04
Expectancy : 166.72%



 -> Average duration trades (jour) : 19.56




--------------------------------------------------------------------------------------------------------------------------------------------------

